In [1]:
import os, pickle
import pandas as pd

In [2]:
import sys
sys.path.append("../../training_data")

In [3]:
from utils.utils import Cif

# Data

In [4]:
with open("../../training_data/7.Extra_set/features.pkl", "rb") as f:
    news = pickle.load(f)

len(news), news

(9,
 {'7gqu':     Residues                                                          \
           pdb label_entity_id label_asym_id label_seq_id auth_asym_id   
  0       7gqu               1             A           12            A   
  1       7gqu               1             A           13            A   
  2       7gqu               1             A           14            A   
  3       7gqu               1             A           15            A   
  4       7gqu               1             A           16            A   
  ..       ...             ...           ...          ...          ...   
  414     7gqu               1             A          426            A   
  415     7gqu               1             A          427            A   
  416     7gqu               1             A          428            A   
  417     7gqu               1             A          429            A   
  418     7gqu               1             A          430            A   
  
                       

In [5]:
with open("../../training_data/7.Extra_set/news_sites.pkl", "rb") as f:
    news_sites = {k: v for k, v in pickle.load(f).items() if k in news}

len(news_sites), news_sites

(9,
 {'7gqu': [{'mod':      label_comp_id label_asym_id label_entity_id label_seq_id  \
    3420           X1L             D               4            .   
    
         pdbx_PDB_ins_code auth_seq_id auth_comp_id auth_asym_id  \
    3420                 ?        1002          X1L            A   
    
         pdbx_PDB_model_num pdbx_label_index pdbx_sifts_xref_db_name  \
    3420                  1             1002                       ?   
    
         pdbx_sifts_xref_db_acc pdbx_sifts_xref_db_num pdbx_sifts_xref_db_res  
    3420                      ?                      ?                      ?  ,
    'site':    label_comp_id label_asym_id label_entity_id label_seq_id pdbx_PDB_ins_code  \
    0            VAL             A               1           55                 ?   
    1            MET             A               1           56                 ?   
    2            ALA             A               1           57                 ?   
    3            THR             A     

# Process structures

In [6]:
os.makedirs("structures", exist_ok=True)

In [7]:
import pymol2

In [8]:
for pdb in news:
    ciff = f"../../training_data/7.Extra_set/cifs/{pdb}.cif"
    if not os.path.isfile(f"structures/{pdb}.cif"):
        os.system(f"cp {ciff} structures/{pdb}.cif")

    if not os.path.isfile(f"structures/{pdb}.pdb"):
        with pymol2.PyMOL() as pymol:
            pymol.cmd.feedback("disable", "executive", "details")
            pymol.cmd.load(ciff, "structure")
            pymol.cmd.save(f"structures/{pdb}.pdb", "structure")

# Our results

In [9]:
from autogluon.tabular import TabularDataset, TabularPredictor

In [10]:
def process_dataframe(df):
    df.index = df["Pockets"][["pdb", "pocket"]].apply(lambda x: "_".join(x), axis=1)
    df = df.drop(columns=["Pockets"], level=0)
    df.columns = map(lambda x: "_".join(x), df.columns.values)
    df.loc[:,'Label_label'] = df['Label_label'].astype("category")
    return df

## Model 5.

In [11]:
predictor = TabularPredictor.load("../pockets_physchem")

In [12]:
with open("../../training_data/7.Extra_set/pockets_features.pkl", "rb") as f:
    extra = pd.concat((
        pickle.load(f).values()
    ))

extra

Pockets                                              Label      FPocket  \
        pdb    pocket nres site_in_pocket pocket_in_site label Pocket Score   
0      7gqu  pocket11   12       0.068966       0.166667     0      -0.1526   
1      7gqu  pocket15   14       0.000000       0.000000     0      -0.3418   
2      7gqu   pocket7   12       0.000000       0.000000     0      -0.0541   
3      7gqu  pocket13   14       0.000000       0.000000     0      -0.1736   
4      7gqu  pocket14   10       0.000000       0.000000     0      -0.1955   
..      ...       ...  ...            ...            ...   ...          ...   
476    9dnm   pocket3   18       0.000000       0.000000     0       0.4903   
477    9dnm  pocket12    9       0.000000       0.000000     0      -0.0091   
478    9dnm  pocket19   12       0.000000       0.000000     0      -0.1447   
479    9dnm  pocket21   12       0.100000       0.083333     0      -0.2238   
480    9dnm   pocket6   14       0.000000       0.000000     0       0.1700   

                                                                 ...  \
    Drug Score Number of alpha spheres Mean alpha-sphere radius  ...   
0       0.0048                    55.0                   3.5579  ...   
1       0.0038                    62.0                   3.8528  ...   
2       0.0013                    40.0                   3.6526  ...   
3       0.0023                    72.0                   3.6145  ...   
4       0.0013                    68.0                   3.5980  ...   
..         ...                     ...                      ...  ...   
476     0.7284                    63.0                   3.1792  ...   
477     0.0024                    38.0                   3.4821  ...   
478     0.1317                    65.0                   3.5098  ...   
479     0.0019                    55.0                   3.6802  ...   
480     0.5809                    64.0                   3.3836  ...   

      HHBlits                                                              \
         M->M      M->I      M->D      I->M      I->I      D->M      D->D   
0    0.955484  0.025227  0.019343  0.165788  0.834238  0.136031  0.863919   
1    0.974569  0.006574  0.018859  0.260971  0.453309  0.306579  0.622019   
2    0.962382  0.023266  0.014359  0.206804  0.543209  0.291031  0.625635   
3    0.962150  0.031724  0.006096  0.232774  0.767232  0.238607  0.761441   
4    0.974479  0.004489  0.021067  0.216619  0.383377  0.343837  0.456162   
..        ...       ...       ...       ...       ...       ...       ...   
476  0.876567  0.062246  0.061196  0.213815  0.508359  0.010684  0.989279   
477  0.993104  0.001887  0.004977  0.310072  0.356584  0.105642  0.894323   
478  0.927772  0.016111  0.056076  0.507445  0.492593  0.249363  0.750681   
479  0.928850  0.010917  0.060229  0.352138  0.647857  0.108113  0.891929   
480  0.990717  0.005898  0.003373  0.265164  0.449084  0.308671  0.691299   

                                    
          Neff    Neff_I    Neff_D  
0    12.327583  1.418000  2.713667  
1    11.424571  0.760786  1.323571  
2    12.056000  1.076917  1.590083  
3    12.314714  1.545143  2.180000  
4    10.979400  0.637500  1.446600  
..         ...       ...       ...  
476   7.976833  0.797944  6.292278  
477   7.297444  0.680889  1.186889  
478   7.837917  1.095000  1.295000  
479   7.866333  1.062083  3.568000  
480   5.812214  0.736286  1.167286  

[245 rows x 194 columns]

In [13]:
# Check that all PDBs only have one positive pocket
extra.assign(totalpos=lambda df: df.groupby(("Pockets", "pdb"))[("Label", "label"),].transform("sum")).iloc[:, [0, -1]].drop_duplicates().sort_values("totalpos")

Pockets totalpos
        pdb         
0      7gqu        1
107    7yg5        1
173    8aq6        1
220    8f4s        1
230    8jp0        1
264    8qni        1
333    8uk6        1
363    8v81        1
459    9dnm        1

In [14]:
extra_probs = predictor.predict_proba( process_dataframe(extra) )
extra_probs

0             1
7gqu_pocket11  0.999350  6.499345e-04
7gqu_pocket15  0.999983  1.690491e-05
7gqu_pocket7   1.000000  1.099709e-07
7gqu_pocket13  0.999502  4.982067e-04
7gqu_pocket14  0.999980  2.031601e-05
...                 ...           ...
9dnm_pocket3   0.999789  2.104968e-04
9dnm_pocket12  0.999416  5.843934e-04
9dnm_pocket19  0.999986  1.404169e-05
9dnm_pocket21  0.999825  1.746797e-04
9dnm_pocket6   0.997017  2.983158e-03

[245 rows x 2 columns]

In [15]:
model5_results = {
    pdb: {
        pocket: {
            "prob": prob,
            "pred": 1 if prob >= 0.5 else 0,
            "label": info[("Label", "label")],
            "max_overlap": overlaps.max(),
            **overlaps["Pockets"].to_dict()
        }
        for pocket in pockets["pocket"]
        for prob in (extra_probs.loc[f"{pdb}_{pocket}", 1],)
        for info in (extra.loc[f"{pdb}_{pocket}"],)
        for overlaps in (info[[("Pockets", "pocket_in_site"), ("Pockets", "site_in_pocket")]],)
    }
    for pdb, pockets in (
        pd.DataFrame(
            extra_probs.index.map(lambda x: x.split("_")).values.tolist(),
            columns=["pdb", "pocket"]
        )
        .groupby("pdb")
    )
}

model5_results

{'7gqu': {'pocket11': {'prob': 0.0006499344599433243,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.16666666666666666,
   'pocket_in_site': 0.16666666666666666,
   'site_in_pocket': 0.06896551724137931},
  'pocket15': {'prob': 1.6904914446058683e-05,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket7': {'prob': 1.0997085553299257e-07,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket13': {'prob': 0.0004982067039236426,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket14': {'prob': 2.0316012523835525e-05,
   'pred': 0,
   'label': 0,
   'max_overlap': 0.0,
   'pocket_in_site': 0.0,
   'site_in_pocket': 0.0},
  'pocket1': {'prob': 0.932378888130188,
   'pred': 1,
   'label': 1,
   'max_overlap': 0.896551724137931,
   'pocket_in_site': 0.21138211382113822,
   'site_in_pocket': 0.896551724137931

In [16]:
pd.DataFrame((
    {
        "pdb": pdb,
        "pocket": pocket,
        **pocketd
    }
    for pdb, pockets in model5_results.items()
    for pocket, pocketd in pockets.items()
)).sort_values("max_overlap", ascending=False).iloc[:40]

pdb    pocket          prob  pred  label  max_overlap  pocket_in_site  \
137  8qni   pocket1  9.183334e-01     1      1     0.966667        0.322222   
194  8v81   pocket1  9.780471e-01     1      1     0.962963        0.208000   
160  8uk6   pocket1  9.466491e-01     1      1     0.952381        0.540541   
5    7gqu   pocket1  9.323789e-01     1      1     0.896552        0.211382   
88   8f4s   pocket1  9.233859e-01     1      1     0.846154        0.733333   
82   8aq6   pocket2  8.510240e-02     0      1     0.812500        0.520000   
236  9dnm   pocket9  2.537859e-05     0      1     0.800000        0.615385   
111  8jp0   pocket1  9.070780e-01     1      1     0.781250        0.320513   
39   7yg5  pocket27  3.324072e-02     0      1     0.730769        0.730769   
132  8qni  pocket11  3.715372e-07     0      0     0.500000        0.500000   
232  9dnm   pocket2  6.564329e-01     1      0     0.500000        0.064103   
7    7gqu   pocket4  4.384644e-04     0      0     0.461538        0.461538   
153  8uk6  pocket15  1.436997e-02     0      0     0.428571        0.428571   
100  8jp0  pocket11  2.890796e-05     0      0     0.400000        0.400000   
101  8jp0  pocket34  2.124135e-05     0      0     0.375000        0.375000   
142  8qni  pocket10  1.049515e-04     0      0     0.375000        0.375000   
122  8jp0   pocket5  8.387357e-05     0      0     0.333333        0.333333   
162  8uk6   pocket2  2.486204e-02     0      0     0.312500        0.312500   
156  8uk6  pocket13  1.861936e-02     0      0     0.294118        0.294118   
11   7gqu   pocket8  4.226042e-05     0      0     0.294118        0.294118   
170  8uk6   pocket5  1.212442e-02     0      0     0.277778        0.277778   
102  8jp0  pocket25  1.733492e-01     0      0     0.250000        0.250000   
19   7yg5  pocket34  4.186362e-07     0      0     0.250000        0.250000   
28   7yg5  pocket22  4.785875e-06     0      0     0.214286        0.214286   
223  9dnm  pocket16  1.012780e-03     0      0     0.200000        0.142857   
0    7gqu  pocket11  6.499345e-04     0      0     0.166667        0.166667   
52   7yg5   pocket5  5.546873e-02     0      0     0.137931        0.105263   
191  8v81  pocket23  5.119030e-04     0      0     0.125000        0.125000   
237  9dnm  pocket10  1.292034e-06     0      0     0.100000        0.100000   
243  9dnm  pocket21  1.746797e-04     0      0     0.100000        0.083333   
226  9dnm  pocket15  1.120616e-04     0      0     0.100000        0.100000   
87   8f4s   pocket7  1.294837e-05     0      0     0.090909        0.090909   
33   7yg5  pocket14  2.483325e-06     0      0     0.090909        0.090909   
130  8jp0   pocket6  1.536785e-05     0      0     0.090909        0.090909   
103  8jp0  pocket15  2.743498e-04     0      0     0.083333        0.083333   
138  8qni   pocket2  9.077860e-07     0      0     0.076923        0.076923   
81   8aq6   pocket1  1.199557e-02     0      0     0.062500        0.047619   
83   8aq6   pocket4  1.274558e-02     0      0     0.062500        0.062500   
145  8qni   pocket3  2.141824e-04     0      0     0.062500        0.062500   
94   8f4s   pocket8  1.785944e-04     0      0     0.050000        0.050000   

     site_in_pocket  
137        0.966667  
194        0.962963  
160        0.952381  
5          0.896552  
88         0.846154  
82         0.812500  
236        0.800000  
111        0.781250  
39         0.655172  
132        0.133333  
232        0.500000  
7          0.206897  
153        0.285714  
100        0.125000  
101        0.187500  
142        0.100000  
122        0.125000  
162        0.238095  
156        0.238095  
11         0.172414  
170        0.238095  
102        0.187500  
19         0.103448  
28         0.103448  
223        0.200000  
0          0.068966  
52         0.137931  
191        0.074074  
237        0.100000  
243        0.100000  
226        0.100000  
87         0.038462  
33         0.034483  
130        0.03125

# Results

## AllositePro

In [17]:
allositepro_resultsf = "AllositePro/allositepro_results.pkl"

with open(allositepro_resultsf, "rb") as f:
    allositepro_results = {k: v for k,v in pickle.load(f).items() if k in news}

len(allositepro_results), allositepro_results

(8,
 {'7gqu': {'pocket0': {'Volume': 425.497,
    'SASA': 211.983,
    'Druggability Score': 0.565,
    'logitProb': 0.564,
    'nmaScore': 0.994,
    'hitScore': 0.65,
    'residues':    auth_asym_id auth_seq_id
    0             A         703
    1             A         849
    2             A         846
    3             A         704
    4             A         845
    5             A         913
    6             A         891
    7             A         916
    8             A         917
    9             A         850
    10            A         728
    11            A         727
    12            A         706
    13            A         895
    14            A         898
    15            A         572
    16            A         570
    17            A         571}},
  '7yg5': {'pocket0': {'Volume': 608.234,
    'SASA': 328.383,
    'Druggability Score': 0.848,
    'logitProb': 0.783,
    'nmaScore': 0.144,
    'hitScore': 0.655,
    'residues':    auth_asym_id auth_seq_i

All output pockets are predicted positive.

In [18]:
allositepro_results = {
    pdb: {
        pocket: {
            "pred": 1,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in allositepro_results.items()
}
allositepro_results

{'7gqu': {'pocket0': {'pred': 1,
   'Volume': 425.497,
   'SASA': 211.983,
   'Druggability Score': 0.565,
   'logitProb': 0.564,
   'nmaScore': 0.994,
   'hitScore': 0.65,
   'residues':    auth_asym_id auth_seq_id
   0             A         703
   1             A         849
   2             A         846
   3             A         704
   4             A         845
   5             A         913
   6             A         891
   7             A         916
   8             A         917
   9             A         850
   10            A         728
   11            A         727
   12            A         706
   13            A         895
   14            A         898
   15            A         572
   16            A         570
   17            A         571}},
 '7yg5': {'pocket0': {'pred': 1,
   'Volume': 608.234,
   'SASA': 328.383,
   'Druggability Score': 0.848,
   'logitProb': 0.783,
   'nmaScore': 0.144,
   'hitScore': 0.655,
   'residues':    auth_asym_id auth_seq_id
   0  

## PASSer

In [19]:
passer_resultsf = "PASSer/passer_results.pkl"

with open(passer_resultsf, "rb") as f:
    passer_results = {k1: {k2: v2 for k2, v2 in v1.items() if k2 in news} for k1, v1 in pickle.load(f).items()}

len(passer_results), tuple(len(v) for v in passer_results.values()), passer_results

(3,
 (9, 9, 9),
 {'ensemble': {'7gqu': {'20': {'prob/score': 50.99665205925703,
     'residues':    auth_asym_id auth_seq_id pdbx_PDB_ins_code
     0             A         916                 ?
     1             A         917                 ?
     4             A         920                 ?
     5             A         727                 ?
     6             A         919                 ?
     8             A         555                 ?
     9             A         552                 ?
     11            A         551                 ?
     12            A         846                 ?
     13            A         845                 ?
     15            A         849                 ?
     17            A         913                 ?
     25            A         706                 ?
     26            A         570                 ?
     27            A         726                 ?
     29            A         725                 ?
     30            A         898         

Top 3 pockets for each PDB are predicted positive.

In [20]:
passer_results = {
    model: {
        pdb: {
            pocket: {
                "pred": 1 if i <=2 else 0,
                **pocketd
            }
            for i, (pocket, pocketd) in enumerate( 
                sorted(
                    pockets.items(), 
                    key=lambda x: x[-1]["prob/score"], 
                    reverse=True
                )
            )
        }
        for pdb, pockets in pdbs.items()
    }
    for model, pdbs in passer_results.items()
}
passer_results

{'ensemble': {'7gqu': {'20': {'pred': 1,
    'prob/score': 50.99665205925703,
    'residues':    auth_asym_id auth_seq_id pdbx_PDB_ins_code
    0             A         916                 ?
    1             A         917                 ?
    4             A         920                 ?
    5             A         727                 ?
    6             A         919                 ?
    8             A         555                 ?
    9             A         552                 ?
    11            A         551                 ?
    12            A         846                 ?
    13            A         845                 ?
    15            A         849                 ?
    17            A         913                 ?
    25            A         706                 ?
    26            A         570                 ?
    27            A         726                 ?
    29            A         725                 ?
    30            A         898                 ?
    31    

## DeepAllo

In [21]:
deepallo_resultsf = "DeepAllo/deepallo_results.pkl"

with open(deepallo_resultsf, "rb") as f:
    deepallo_results = pickle.load(f)

len(deepallo_results), deepallo_results

(9,
 {'7gqu': {0: {'pred': 1,
    'prob': 0.2415745109319687,
    'residues':    auth_asym_id auth_seq_id
    0             A         800
    1             A         807
    2             A         859
    3             A         826
    4             A         824
    ..          ...         ...
    73            A         597
    74            A         548
    75            A         825
    76            A         828
    77            A         888
    
    [78 rows x 2 columns]},
   1: {'pred': 1,
    'prob': 0.1223275363445282,
    'residues':    auth_asym_id auth_seq_id
    0             A         895
    1             A         913
    2             A         920
    3             A         914
    4             A         916
    5             A         571
    6             A         728
    7             A         575
    8             A         555
    9             A         891
    10            A         552
    11            A         918
    12            A         730

In [22]:
deepallo_results = {
    pdb: {
        pocket: {
            "prob": 0, # will be replaced by the real prob of the top3 pockets if it's in pocketd
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in deepallo_results.items()
}
deepallo_results

{'7gqu': {0: {'prob': 0.2415745109319687,
   'pred': 1,
   'residues':    auth_asym_id auth_seq_id
   0             A         800
   1             A         807
   2             A         859
   3             A         826
   4             A         824
   ..          ...         ...
   73            A         597
   74            A         548
   75            A         825
   76            A         828
   77            A         888
   
   [78 rows x 2 columns]},
  1: {'prob': 0.1223275363445282,
   'pred': 1,
   'residues':    auth_asym_id auth_seq_id
   0             A         895
   1             A         913
   2             A         920
   3             A         914
   4             A         916
   5             A         571
   6             A         728
   7             A         575
   8             A         555
   9             A         891
   10            A         552
   11            A         918
   12            A         730
   13            A         845
   1

## STINGAllo

In [23]:
stingallo_resultsf = "STINGAllo/stingallo_results.pkl"

with open(stingallo_resultsf, "rb") as f:
    stingallo_results = pickle.load(f)

len(stingallo_results), stingallo_results

(2,
 {'8qni': {'pocket': {'residues':   auth_asym_id auth_seq_id
    0            A         148}},
  '7gqu': {'pocket': {'residues':   auth_asym_id auth_seq_id
    0            A         574
    1            A         576}}})

In [24]:
stingallo_results = {
    pdb: {
        pocket: {
            "pred": 1,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in stingallo_results.items()
}
stingallo_results

{'8qni': {'pocket': {'pred': 1,
   'residues':   auth_asym_id auth_seq_id
   0            A         148}},
 '7gqu': {'pocket': {'pred': 1,
   'residues':   auth_asym_id auth_seq_id
   0            A         574
   1            A         576}}}

## AllosES

In [25]:
alloses_resultsf = "AllosES/alloses_results.pkl"

with open(alloses_resultsf, "rb") as f:
    alloses_results = pickle.load(f)

len(alloses_results), alloses_results

(9,
 {'7gqu': {'pocket7': {'pro_ave': 0.6077189166132947,
    'residues':    auth_seq_id auth_asym_id
    0          601            A
    1          829            A
    2          573            A
    3          577            A
    4          578            A
    ..         ...          ...
    73         923            A
    74         551            A
    75         547            A
    76         883            A
    77         801            A
    
    [78 rows x 2 columns]},
   'pocket20': {'pro_ave': 0.4671694797381203,
    'residues':    auth_seq_id auth_asym_id
    0          916            A
    1          917            A
    2          920            A
    3          727            A
    4          919            A
    5          555            A
    6          552            A
    7          551            A
    8          846            A
    9          845            A
    10         849            A
    11         913            A
    12         706            A
    13

Positive preds. above 0.5 probability (average).

In [26]:
alloses_results = {
    pdb: {
        pocket: {
            "pred": 1 if pocketd["pro_ave"] >= 0.5 else 0,
            **pocketd
        }
        for pocket, pocketd in pockets.items()
    }
    for pdb, pockets in alloses_results.items()
}
alloses_results

{'7gqu': {'pocket7': {'pred': 1,
   'pro_ave': 0.6077189166132947,
   'residues':    auth_seq_id auth_asym_id
   0          601            A
   1          829            A
   2          573            A
   3          577            A
   4          578            A
   ..         ...          ...
   73         923            A
   74         551            A
   75         547            A
   76         883            A
   77         801            A
   
   [78 rows x 2 columns]},
  'pocket20': {'pred': 0,
   'pro_ave': 0.4671694797381203,
   'residues':    auth_seq_id auth_asym_id
   0          916            A
   1          917            A
   2          920            A
   3          727            A
   4          919            A
   5          555            A
   6          552            A
   7          551            A
   8          846            A
   9          845            A
   10         849            A
   11         913            A
   12         706            A
   13       

## MEF-AlloSite

In [27]:
import json

In [28]:
mefallosite_resultsf = "MEF-AlloSite/mef-allosite_results.json"

with open(mefallosite_resultsf, "r") as f:
    mefallosite_results = json.load(f)

len(mefallosite_results), mefallosite_results

(9,
 {'7gqu': {'pocket15': {'prob': 0.07944463348637025,
    'pred': 0,
    'residues': {'auth_asym_id': ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A'],
     'auth_seq_id': ['760',
      '762',
      '766',
      '790',
      '813',
      '814',
      '815',
      '816',
      '832'],
     'pdbx_PDB_ins_code': ['?', '?', '?', '?', '?', '?', '?', '?', '?']}},
   'pocket21': {'prob': 0.09888412648191054,
    'pred': 0,
    'residues': {'auth_asym_id': ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A'],
     'auth_seq_id': ['561', '564', '588', '590', '657', '661', '662', '663'],
     'pdbx_PDB_ins_code': ['?', '?', '?', '?', '?', '?', '?', '?']}},
   'pocket22': {'prob': 0.20238072673479715,
    'pred': 0,
    'residues': {'auth_asym_id': ['A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A',
      'A'],
     'auth_seq_id': ['740',
      '752',
      '753',
      '763',
      '764',
      '765',
      '767',
      '834',
      

In [29]:
mefallosite_results = {
    pdb: {
        pocket: {
            k: v if k != "residues" else pd.DataFrame(v)
            for k, v in pocketd.items()
        }
        for pocket, pocketd in pockets.items()
    } 
    for pdb, pockets in mefallosite_results.items()
}

mefallosite_results

{'7gqu': {'pocket15': {'prob': 0.07944463348637025,
   'pred': 0,
   'residues':   auth_asym_id auth_seq_id pdbx_PDB_ins_code
   0            A         760                 ?
   1            A         762                 ?
   2            A         766                 ?
   3            A         790                 ?
   4            A         813                 ?
   5            A         814                 ?
   6            A         815                 ?
   7            A         816                 ?
   8            A         832                 ?},
  'pocket21': {'prob': 0.09888412648191054,
   'pred': 0,
   'residues':   auth_asym_id auth_seq_id pdbx_PDB_ins_code
   0            A         561                 ?
   1            A         564                 ?
   2            A         588                 ?
   3            A         590                 ?
   4            A         657                 ?
   5            A         661                 ?
   6            A         662     

## ALLO

In [30]:
allo_resultsf = "ALLO/ALLO_results.json"

with open(allo_resultsf, "r") as f:
    allo_results = json.load(f)

len(allo_results), allo_results

(9,
 {'9dnm': {'P_10': {'pred': 0,
    'prob': 0.02444,
    'residues': {'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?'],
     'auth_asym_id': ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A'],
     'auth_seq_id': ['58',
      '59',
      '60',
      '62',
      '76',
      '78',
      '143',
      '144',
      '145',
      '147',
      '165']}},
   'P_11': {'pred': 0,
    'prob': 0.02447,
    'residues': {'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?'],
     'auth_asym_id': ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A'],
     'auth_seq_id': ['341',
      '342',
      '343',
      '344',
      '345',
      '347',
      '348',
      '413',
      '414']}},
   'P_12': {'pred': 0,
    'prob': 0.02444,
    'residues': {'pdbx_PDB_ins_code': ['?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?',
      '?'],

In [31]:
allo_results = {
    pdb: {
        pocket: {
            k: v if k != "residues" else pd.DataFrame(v)
            for k, v in pocketd.items()
        }
        for pocket, pocketd in pockets.items()
    } 
    for pdb, pockets in allo_results.items()
}

allo_results

{'9dnm': {'P_10': {'pred': 0,
   'prob': 0.02444,
   'residues':    pdbx_PDB_ins_code auth_asym_id auth_seq_id
   0                  ?            A          58
   1                  ?            A          59
   2                  ?            A          60
   3                  ?            A          62
   4                  ?            A          76
   5                  ?            A          78
   6                  ?            A         143
   7                  ?            A         144
   8                  ?            A         145
   9                  ?            A         147
   10                 ?            A         165},
  'P_11': {'pred': 0,
   'prob': 0.02447,
   'residues':   pdbx_PDB_ins_code auth_asym_id auth_seq_id
   0                 ?            A         341
   1                 ?            A         342
   2                 ?            A         343
   3                 ?            A         344
   4                 ?            A         345
   5  

## All models

In [32]:
defaults = { "all_pockets_in_output": True, "prob_key": "prob" }

models = {
    "model5": { "results": model5_results, **defaults, "labelling": None },
    
    "allositepro": { "results": allositepro_results, "all_pockets_in_output": False, "prob_key": "hitScore" },
    "stingallo": { "results": stingallo_results, "all_pockets_in_output": False, "prob_key": None },
    
    "passer_ensemble": { "results": passer_results["ensemble"], **defaults, "prob_key": "prob/score" },
    "passer_automl": { "results": passer_results["automl"], **defaults, "prob_key": "prob/score" },
    "passer_rank": { "results": passer_results["rank"], **defaults, "prob_key": "prob/score" },
    "deepallo": { "results": deepallo_results, **defaults },
    "alloses": { "results": alloses_results, **defaults, "prob_key": "pro_ave" },
    "mefallosite": { "results": mefallosite_results, **defaults },
    "allo": { "results": allo_results, **defaults },
}
models

{'model5': {'results': {'7gqu': {'pocket11': {'prob': 0.0006499344599433243,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.16666666666666666,
     'pocket_in_site': 0.16666666666666666,
     'site_in_pocket': 0.06896551724137931},
    'pocket15': {'prob': 1.6904914446058683e-05,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket7': {'prob': 1.0997085553299257e-07,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket13': {'prob': 0.0004982067039236426,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket14': {'prob': 2.0316012523835525e-05,
     'pred': 0,
     'label': 0,
     'max_overlap': 0.0,
     'pocket_in_site': 0.0,
     'site_in_pocket': 0.0},
    'pocket1': {'prob': 0.932378888130188,
     'pred': 1,
     'label': 1,
     'max_overlap': 0.89655172

# Labelling

In [33]:
# Percentage of residues of "one" in "other"
get_overlap = lambda one, other: (
    len( one.merge(other) ) / len(one)
)

get_overlaps = lambda pdb, pocketd: {
    name: get_overlap(*one_in_other) 
        for site in news_sites[pdb] 
            for name, one_in_other in (
                ("pocket_in_site", (pocketd["residues"], site["site"])),
                ("site_in_pocket", (site["site"], pocketd["residues"])),
            )
}

def get_label(overlaps, site_in_pocket=None, pocket_in_site=None):
    assert not (site_in_pocket==None and pocket_in_site==None)
    
    if site_in_pocket is None:
        return int( overlaps["pocket_in_site"] >= pocket_in_site )
    if pocket_in_site is None:
        return int( overlaps["site_in_pocket"] >= site_in_pocket )
    return int( overlaps["site_in_pocket"] >= site_in_pocket or overlaps["pocket_in_site"] >= pocket_in_site )

In [34]:
# def label_results(resultsd, site_in_pocket=0.65, pocket_in_site=None, prob_key=None):
#     return pd.DataFrame((
#         {
#             "pdb": pdb,
#             "pocket": pocket,
#             **{"prob": pocketd[prob_key] for prob_key in (prob_key,) if prob_key is not None},
#             "pred": pocketd["pred"],
#             "label": get_label(overlaps, site_in_pocket, pocket_in_site),
#             "max_overlap": max(overlaps.values()),
#             **overlaps,
#         }
#         for pdb, pockets in resultsd.items()
#         for pocket, pocketd in pockets.items()
#         for overlaps in (get_overlaps(pdb, pocketd),)
#     )).sort_values("max_overlap", ascending=False)

In [35]:
def label_results(resultsd, site_in_pocket=0.65, pocket_in_site=None, prob_key=None):
    df = pd.DataFrame((
        {
            "pdb": pdb,
            "pocket": pocket,
            **{"prob": pocketd[prob_key] for prob_key in (prob_key,) if prob_key is not None},
            "pred": pocketd["pred"],
            "label": get_label(overlaps, site_in_pocket, pocket_in_site),
            "max_overlap": max(overlaps.values()),
            **overlaps,
        }
        for pdb, pockets in resultsd.items()
        for pocket, pocketd in pockets.items()
        for overlaps in (get_overlaps(pdb, pocketd),)
    ))
    if prob_key is not None:
        df["pred"] = (
            # Start from a Series where each value/row (sample/pocket) is the total number of pos. labels on its PDB
            df.groupby("pdb")["label"].transform("sum")
            # Then subtract this "total num. of pos. in a PDB" by the rank of each pocket in a PDB, sorted by the probability
            .sub(df.groupby("pdb")["prob"].rank(method="first", ascending=False))
            # If the subtraction is positive or 0 it means that the pocket is in the topX and will be assigned 1
            >= 0
        ).astype(int)
        # If a PDB has no + labelled pocket, assign the highest prob. as positive
        for pdb, group in df.groupby("pdb"):
            if group["pred"].sum() == 0:
                df.loc[ group["prob"].idxmax(), "pred" ] = 1
            
    
    return df.sort_values("max_overlap", ascending=False)

## AllositePro

In [36]:
label_results(allositepro_results, site_in_pocket=0.65, pocket_in_site=0.8)

pdb   pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
0  7gqu  pocket0     1      1     1.000000        1.000000        0.620690
4  8jp0  pocket0     1      1     1.000000        1.000000        0.312500
7  8uk6  pocket1     1      1     0.952381        0.833333        0.952381
5  8qni  pocket0     1      1     0.933333        0.608696        0.933333
3  8f4s  pocket0     1      1     0.846154        0.733333        0.846154
8  8v81  pocket0     1      1     0.800000        0.800000        0.444444
6  8uk6  pocket0     1      0     0.047619        0.031250        0.047619
1  7yg5  pocket0     1      0     0.000000        0.000000        0.000000
2  8aq6  pocket0     1      0     0.000000        0.000000        0.000000

In [37]:
models["allositepro"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

## PASSer

In [38]:
label_results(passer_results["ensemble"], site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
253  8uk6      1     1      1     0.904762        0.904762        0.904762
297  8v81     49     1      1     0.888889        0.666667        0.888889
232  8qni     13     1      1     0.833333        0.510204        0.833333
0    7gqu     20     1      1     0.758621        0.687500        0.758621
149  8f4s      9     1      1     0.730769        0.730769        0.730769
173  8jp0     57     1      1     0.718750        0.534884        0.718750
31   7yg5     29     0      1     0.708333        0.708333        0.586207
141  8aq6      1     1      0     0.666667        0.666667        0.375000
157  8f4s     15     0      0     0.625000        0.625000        0.192308
241  8qni      1     0      0     0.428571        0.428571        0.200000
148  8aq6      4     0      0     0.428571        0.428571        0.187500
382  9dnm      3     0      0     0.400000        0.400000        0.400000
283  8uk6     34     0      0     0.400000        0.400000        0.095238
267  8uk6      7     0      0     0.384615        0.384615        0.238095
86   7yg5     23     0      0     0.375000        0.375000        0.103448
191  8jp0     14     0      0     0.375000        0.375000        0.093750
18   7gqu      3     0      0     0.333333        0.333333        0.103448
90   7yg5     34     0      0     0.333333        0.333333        0.068966
233  8qni     19     1      0     0.307692        0.307692        0.266667
317  8v81      8     0      0     0.307692        0.307692        0.148148
290  8uk6     36     0      0     0.300000        0.300000        0.142857
208  8jp0      5     0      0     0.300000        0.300000        0.093750
390  9dnm     30     0      0     0.285714        0.285714        0.200000
174  8jp0     59     1      0     0.285714        0.285714        0.125000
160  8f4s      7     0      0     0.250000        0.250000        0.076923
1    7gqu      7     1      0     0.241379        0.089744        0.241379
177  8jp0     47     0      0     0.238095        0.238095        0.156250
257  8uk6      8     0      0     0.230769        0.230769        0.142857
169  8f4s     21     0      0     0.222222        0.222222        0.076923
6    7gqu     17     0      0     0.200000        0.200000        0.068966
270  8uk6      5     0      0     0.200000        0.200000        0.095238
361  8v81     29     0      0     0.181818        0.181818        0.074074
303  8v81      2     0      0     0.153846        0.153846        0.074074
218  8jp0     31     0      0     0.142857        0.142857        0.031250
15   7gqu     12     0      0     0.142857        0.142857        0.034483
106  7yg5     95     0      0     0.125000        0.125000        0.034483
282  8uk6     30     0      0     0.125000        0.125000        0.047619
384  9dnm     16     0      0     0.125000        0.125000        0.100000
249  8qni     16     0      0     0.125000        0.125000        0.033333
145  8aq6      9     0      0     0.125000        0.125000        0.062500

In [39]:
models["passer_ensemble"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

In [40]:
label_results(passer_results["automl"], site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
253  8uk6      1     1      1     0.904762        0.904762        0.904762
298  8v81     49     0      1     0.888889        0.666667        0.888889
232  8qni     13     1      1     0.833333        0.510204        0.833333
1    7gqu     20     1      1     0.758621        0.687500        0.758621
149  8f4s      9     1      1     0.730769        0.730769        0.730769
173  8jp0     57     1      1     0.718750        0.534884        0.718750
31   7yg5     29     0      1     0.708333        0.708333        0.586207
141  8aq6      1     1      0     0.666667        0.666667        0.375000
155  8f4s     15     0      0     0.625000        0.625000        0.192308
239  8qni      1     0      0     0.428571        0.428571        0.200000
143  8aq6      4     0      0     0.428571        0.428571        0.187500
384  9dnm      3     0      0     0.400000        0.400000        0.400000
280  8uk6     34     0      0     0.400000        0.400000        0.095238
270  8uk6      7     0      0     0.384615        0.384615        0.238095
128  7yg5     23     0      0     0.375000        0.375000        0.103448
198  8jp0     14     0      0     0.375000        0.375000        0.093750
78   7yg5     34     0      0     0.333333        0.333333        0.068966
9    7gqu      3     0      0     0.333333        0.333333        0.103448
321  8v81      8     0      0     0.307692        0.307692        0.148148
233  8qni     19     1      0     0.307692        0.307692        0.266667
276  8uk6     36     0      0     0.300000        0.300000        0.142857
199  8jp0      5     0      0     0.300000        0.300000        0.093750
174  8jp0     59     1      0     0.285714        0.285714        0.125000
391  9dnm     30     0      0     0.285714        0.285714        0.200000
171  8f4s      7     0      0     0.250000        0.250000        0.076923
0    7gqu      7     1      0     0.241379        0.089744        0.241379
175  8jp0     47     1      0     0.238095        0.238095        0.156250
266  8uk6      8     0      0     0.230769        0.230769        0.142857
151  8f4s     21     1      0     0.222222        0.222222        0.076923
2    7gqu     17     1      0     0.200000        0.200000        0.068966
269  8uk6      5     0      0     0.200000        0.200000        0.095238
315  8v81     29     0      0     0.181818        0.181818        0.074074
305  8v81      2     0      0     0.153846        0.153846        0.074074
19   7gqu     12     0      0     0.142857        0.142857        0.034483
210  8jp0     31     0      0     0.142857        0.142857        0.031250
97   7yg5     95     0      0     0.125000        0.125000        0.034483
379  9dnm     16     0      0     0.125000        0.125000        0.100000
265  8uk6     30     0      0     0.125000        0.125000        0.047619
250  8qni     16     0      0     0.125000        0.125000        0.033333
148  8aq6      9     0      0     0.125000        0.125000        0.062500

In [41]:
models["passer_automl"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

In [42]:
label_results(passer_results["rank"], site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
253  8uk6      1     1      1     0.904762        0.904762        0.904762
316  8v81     49     0      1     0.888889        0.666667        0.888889
240  8qni     13     0      1     0.833333        0.510204        0.833333
3    7gqu     20     0      1     0.758621        0.687500        0.758621
151  8f4s      9     1      1     0.730769        0.730769        0.730769
189  8jp0     57     0      1     0.718750        0.534884        0.718750
80   7yg5     29     0      1     0.708333        0.708333        0.586207
143  8aq6      1     0      0     0.666667        0.666667        0.375000
168  8f4s     15     0      0     0.625000        0.625000        0.192308
142  8aq6      4     1      0     0.428571        0.428571        0.187500
232  8qni      1     1      0     0.428571        0.428571        0.200000
281  8uk6     34     0      0     0.400000        0.400000        0.095238
378  9dnm      3     0      0     0.400000        0.400000        0.400000
264  8uk6      7     0      0     0.384615        0.384615        0.238095
51   7yg5     23     0      0     0.375000        0.375000        0.103448
198  8jp0     14     0      0     0.375000        0.375000        0.093750
19   7gqu      3     0      0     0.333333        0.333333        0.103448
85   7yg5     34     0      0     0.333333        0.333333        0.068966
238  8qni     19     0      0     0.307692        0.307692        0.266667
350  8v81      8     0      0     0.307692        0.307692        0.148148
271  8uk6     36     0      0     0.300000        0.300000        0.142857
196  8jp0      5     0      0     0.300000        0.300000        0.093750
393  9dnm     30     0      0     0.285714        0.285714        0.200000
183  8jp0     59     0      0     0.285714        0.285714        0.125000
169  8f4s      7     0      0     0.250000        0.250000        0.076923
1    7gqu      7     1      0     0.241379        0.089744        0.241379
192  8jp0     47     0      0     0.238095        0.238095        0.156250
260  8uk6      8     0      0     0.230769        0.230769        0.142857
161  8f4s     21     0      0     0.222222        0.222222        0.076923
9    7gqu     17     0      0     0.200000        0.200000        0.068966
255  8uk6      5     1      0     0.200000        0.200000        0.095238
315  8v81     29     0      0     0.181818        0.181818        0.074074
296  8v81      2     1      0     0.153846        0.153846        0.074074
181  8jp0     31     0      0     0.142857        0.142857        0.031250
13   7gqu     12     0      0     0.142857        0.142857        0.034483
249  8qni     16     0      0     0.125000        0.125000        0.033333
147  8aq6      9     0      0     0.125000        0.125000        0.062500
108  7yg5     95     0      0     0.125000        0.125000        0.034483
401  9dnm     16     0      0     0.125000        0.125000        0.100000
263  8uk6     30     0      0     0.125000        0.125000        0.047619

In [43]:
models["passer_rank"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

## DeepAllo

In [44]:
label_results(deepallo_results, site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb  pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
254  8uk6       0     1      1     0.904762        0.904762        0.904762
297  8v81       1     1      1     0.888889        0.666667        0.888889
233  8qni       1     1      1     0.833333        0.543478        0.833333
1    7gqu       1     1      1     0.758621        0.687500        0.758621
149  8f4s       0     1      1     0.730769        0.730769        0.730769
221  8jp0      48     0      1     0.718750        0.534884        0.718750
62   7yg5      35     0      1     0.708333        0.708333        0.586207
141  8aq6       1     1      0     0.666667        0.666667        0.375000
166  8f4s      17     0      0     0.625000        0.625000        0.192308
232  8qni       0     1      0     0.428571        0.428571        0.200000
146  8aq6       6     0      0     0.428571        0.428571        0.187500
292  8uk6      38     0      0     0.400000        0.400000        0.095238
383  9dnm      13     0      0     0.400000        0.400000        0.400000
256  8uk6       2     1      0     0.384615        0.384615        0.238095
177  8jp0       4     0      0     0.375000        0.375000        0.093750
37   7yg5      10     0      0     0.375000        0.375000        0.103448
119  7yg5      92     0      0     0.333333        0.333333        0.068966
12   7gqu      12     0      0     0.333333        0.333333        0.103448
328  8v81      32     0      0     0.307692        0.307692        0.148148
244  8qni      12     0      0     0.307692        0.307692        0.266667
279  8uk6      25     0      0     0.300000        0.300000        0.142857
197  8jp0      24     0      0     0.300000        0.300000        0.093750
391  9dnm      21     0      0     0.285714        0.285714        0.200000
206  8jp0      33     0      0     0.285714        0.285714        0.125000
169  8f4s      20     0      0     0.250000        0.250000        0.076923
0    7gqu       0     1      0     0.241379        0.089744        0.241379
223  8jp0      50     0      0     0.238095        0.238095        0.156250
282  8uk6      28     0      0     0.230769        0.230769        0.142857
153  8f4s       4     0      0     0.222222        0.222222        0.076923
14   7gqu      14     0      0     0.200000        0.200000        0.068966
284  8uk6      30     0      0     0.200000        0.200000        0.095238
331  8v81      35     0      0     0.181818        0.181818        0.074074
361  8v81      65     0      0     0.153846        0.153846        0.074074
228  8jp0      55     0      0     0.142857        0.142857        0.031250
20   7gqu      20     0      0     0.142857        0.142857        0.034483
243  8qni      11     0      0     0.125000        0.125000        0.033333
272  8uk6      18     0      0     0.125000        0.125000        0.047619
373  9dnm       3     0      0     0.125000        0.125000        0.100000
147  8aq6       7     0      0     0.125000        0.125000        0.062500
54   7yg5      27     0      0     0.125000        0.125000        0.034483

In [45]:
models["deepallo"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

## STINGAllo

In [46]:
label_results(stingallo_results, site_in_pocket=None, pocket_in_site=1)

pdb  pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
0  8qni  pocket     1      1          1.0             1.0        0.033333
1  7gqu  pocket     1      0          0.0             0.0        0.000000

In [47]:
models["stingallo"]["labelling"] = {"site_in_pocket": None, "pocket_in_site": 1}

## AllosES

In [48]:
label_results(alloses_results, site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb    pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
253  8uk6   pocket1     0      1     0.904762        0.904762        0.904762
296  8v81  pocket49     0      1     0.888889        0.666667        0.888889
231  8qni  pocket13     0      1     0.833333        0.510204        0.833333
1    7gqu  pocket20     0      1     0.758621        0.687500        0.758621
147  8f4s   pocket9     1      1     0.730769        0.730769        0.730769
171  8jp0  pocket57     1      1     0.718750        0.534884        0.718750
45   7yg5  pocket29     0      1     0.708333        0.708333        0.586207
140  8aq6   pocket1     0      0     0.666667        0.666667        0.375000
161  8f4s  pocket15     0      0     0.625000        0.625000        0.192308
146  8aq6   pocket4     0      0     0.428571        0.428571        0.187500
232  8qni   pocket1     0      0     0.428571        0.428571        0.200000
271  8uk6  pocket34     0      0     0.400000        0.400000        0.095238
394  9dnm   pocket3     0      0     0.400000        0.400000        0.400000
280  8uk6   pocket7     0      0     0.384615        0.384615        0.238095
50   7yg5  pocket23     0      0     0.375000        0.375000        0.103448
175  8jp0  pocket14     0      0     0.375000        0.375000        0.093750
19   7gqu   pocket3     0      0     0.333333        0.333333        0.103448
73   7yg5  pocket34     0      0     0.333333        0.333333        0.068966
310  8v81   pocket8     0      0     0.307692        0.307692        0.148148
233  8qni  pocket19     0      0     0.307692        0.307692        0.266667
176  8jp0   pocket5     0      0     0.300000        0.300000        0.093750
274  8uk6  pocket36     0      0     0.300000        0.300000        0.142857
196  8jp0  pocket60     0      0     0.285714        0.285714        0.125000
380  9dnm  pocket30     0      0     0.285714        0.285714        0.200000
163  8f4s   pocket7     0      0     0.250000        0.250000        0.076923
0    7gqu   pocket7     1      0     0.241379        0.089744        0.241379
172  8jp0  pocket47     0      0     0.238095        0.238095        0.156250
256  8uk6   pocket8     0      0     0.230769        0.230769        0.142857
170  8f4s  pocket21     0      0     0.222222        0.222222        0.076923
254  8uk6   pocket5     0      0     0.200000        0.200000        0.095238
3    7gqu  pocket17     0      0     0.200000        0.200000        0.068966
319  8v81  pocket29     0      0     0.181818        0.181818        0.074074
306  8v81   pocket2     0      0     0.153846        0.153846        0.074074
12   7gqu  pocket12     0      0     0.142857        0.142857        0.034483
177  8jp0  pocket32     0      0     0.142857        0.142857        0.031250
237  8qni  pocket16     0      0     0.125000        0.125000        0.033333
88   7yg5  pocket93     0      0     0.125000        0.125000        0.034483
398  9dnm  pocket16     0      0     0.125000        0.125000        0.100000
141  8aq6   pocket9     0      0     0.125000        0.125000        0.062500
287  8uk6  pocket30     0      0     0.125000        0.125000        0.047619

In [49]:
models["alloses"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

## MEF-AlloSite

In [50]:
label_results(mefallosite_results, site_in_pocket=0.65, pocket_in_site=0.7).iloc[:40]

pdb    pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
234  8uk6   pocket1     0      1     0.904762        0.904762        0.904762
278  8v81  pocket36     0      1     0.888889        0.666667        0.888889
200  8qni  pocket13     0      1     0.833333        0.510204        0.833333
17   7gqu  pocket14     1      1     0.758621        0.687500        0.758621
124  8f4s   pocket8     1      1     0.720000        0.720000        0.692308
175  8jp0  pocket49     0      1     0.718750        0.534884        0.718750
55   7yg5  pocket12     0      1     0.708333        0.708333        0.586207
110  8aq6   pocket1     1      0     0.666667        0.666667        0.375000
117  8f4s  pocket16     0      0     0.625000        0.625000        0.192308
6    7gqu   pocket3     0      0     0.454545        0.454545        0.172414
201  8qni   pocket1     0      0     0.428571        0.428571        0.200000
109  8aq6   pocket5     0      0     0.428571        0.428571        0.187500
215  8uk6  pocket27     0      0     0.400000        0.400000        0.095238
312  9dnm   pocket3     0      0     0.400000        0.400000        0.400000
241  8uk6   pocket7     0      0     0.384615        0.384615        0.238095
173  8jp0  pocket13     0      0     0.375000        0.375000        0.093750
41   7yg5  pocket16     0      0     0.375000        0.375000        0.103448
18   7gqu   pocket4     0      0     0.333333        0.333333        0.103448
265  8v81   pocket6     0      0     0.333333        0.333333        0.148148
61   7yg5  pocket20     0      0     0.333333        0.333333        0.068966
207  8qni  pocket19     1      0     0.307692        0.307692        0.266667
171  8jp0   pocket5     0      0     0.300000        0.300000        0.093750
221  8uk6  pocket29     0      0     0.300000        0.300000        0.142857
116  8f4s  pocket10     0      0     0.285714        0.285714        0.076923
129  8f4s  pocket14     0      0     0.285714        0.285714        0.076923
157  8jp0  pocket52     0      0     0.285714        0.285714        0.125000
321  9dnm  pocket28     0      0     0.285714        0.285714        0.200000
178  8jp0  pocket41     0      0     0.238095        0.238095        0.156250
229  8uk6   pocket8     0      0     0.230769        0.230769        0.142857
231  8uk6   pocket5     0      0     0.200000        0.200000        0.095238
5    7gqu  pocket16     0      0     0.200000        0.200000        0.068966
295  8v81   pocket4     0      0     0.200000        0.200000        0.074074
246  8v81  pocket21     0      0     0.181818        0.181818        0.074074
153  8jp0  pocket29     0      0     0.142857        0.142857        0.031250
15   7gqu  pocket13     0      0     0.142857        0.142857        0.034483
4    7gqu  pocket23     0      0     0.137931        0.059701        0.137931
112  8aq6   pocket7     0      0     0.125000        0.125000        0.062500
190  8qni  pocket16     0      0     0.125000        0.125000        0.033333
42   7yg5  pocket68     0      0     0.125000        0.125000        0.034483
179  8jp0   pocket4     0      0     0.111111        0.111111        0.031250

In [51]:
models["mefallosite"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": 0.7}

## ALLO

In [52]:
label_results(allo_results, site_in_pocket=0.65, pocket_in_site=None).iloc[:40]

pdb pocket  pred  label  max_overlap  pocket_in_site  site_in_pocket
42   8uk6    P_0     0      1     1.000000        0.375000        1.000000
22   8qni    P_0     1      1     1.000000        0.312500        1.000000
189  8jp0    P_0     1      1     0.968750        0.248000        0.968750
168  7gqu    P_1     0      1     0.950000        0.950000        0.655172
155  8v81    P_0     1      1     0.925926        0.500000        0.925926
112  8f4s    P_0     0      1     0.846154        0.758621        0.846154
12   9dnm    P_0     1      1     0.700000        0.066038        0.700000
93   7yg5    P_1     1      1     0.655172        0.513514        0.655172
65   7yg5   P_39     0      0     0.500000        0.500000        0.137931
165  7gqu    P_2     0      0     0.333333        0.333333        0.206897
134  8v81   P_13     0      0     0.318182        0.318182        0.259259
167  7gqu    P_0     1      0     0.310345        0.152542        0.310345
106  8f4s    P_6     0      0     0.294118        0.294118        0.192308
87   7yg5    P_7     0      0     0.166667        0.166667        0.137931
117  8v81   P_20     0      0     0.142857        0.142857        0.074074
43   8uk6    P_1     1      0     0.142857        0.066667        0.142857
95   8aq6    P_2     1      0     0.125000        0.111111        0.125000
177  8jp0   P_16     0      0     0.117647        0.117647        0.062500
119  8v81   P_22     0      0     0.100000        0.100000        0.037037
96   8aq6    P_3     0      0     0.090909        0.090909        0.062500
110  8f4s    P_2     0      0     0.090909        0.090909        0.076923
159  7gqu    P_8     0      0     0.090909        0.090909        0.034483
139  8v81   P_18     0      0     0.076923        0.076923        0.037037
113  8f4s    P_1     0      0     0.076923        0.074074        0.076923
98   8aq6    P_1     0      0     0.071429        0.071429        0.062500
69   7yg5   P_11     0      0     0.058824        0.058824        0.034483
21   8qni    P_3     0      0     0.052632        0.052632        0.033333
39   8uk6    P_5     0      0     0.047619        0.045455        0.047619
166  7gqu    P_3     0      0     0.045455        0.045455        0.034483
91   7yg5    P_3     0      0     0.035714        0.035714        0.034483
132  8v81   P_11     0      0     0.000000        0.000000        0.000000
129  8v81   P_36     0      0     0.000000        0.000000        0.000000
133  8v81   P_12     0      0     0.000000        0.000000        0.000000
128  8v81   P_17     0      0     0.000000        0.000000        0.000000
135  8v81   P_14     0      0     0.000000        0.000000        0.000000
127  8v81   P_38     0      0     0.000000        0.000000        0.000000
131  8v81   P_10     0      0     0.000000        0.000000        0.000000
136  8v81   P_15     0      0     0.000000        0.000000        0.000000
125  8v81   P_41     0      0     0.000000        0.000000        0.000000
126  8v81   P_40     0      0     0.000000        0.000000        0.000000

In [53]:
models["allo"]["labelling"] = {"site_in_pocket": 0.65, "pocket_in_site": None}

<br>

In [54]:
pd.to_pickle(models, "models.pkl")

# Scoring

In [65]:
models_preds = {}

for model, modeld in models.items():
    results = modeld["results"]
    if modeld["labelling"] is not None:
        labelled_results = label_results(results, **modeld["labelling"], prob_key=modeld["prob_key"])
    else:
        labelled_results = pd.DataFrame((
            {
                "pdb": pdb,
                "pocket": pocket,
                **pocketd
            }
            for pdb, pockets in results.items()
            for pocket, pocketd in pockets.items()
        ))

    preds = {}
    for pdb in news:
        pdbpreds = labelled_results.query(f"pdb == '{pdb}'")
        total = len(pdbpreds)
        if total > 0:
            # Top1 pred for our model
            if model == "model5":
                pdbpreds.loc[:, "pred"] = pdbpreds[["prob"]].apply(lambda x: (x == x.max()).astype(int)).values
            tp = len( pdbpreds.loc[lambda x: (x["pred"] == 1) & (x["label"] == 1)] )
            fp = len( pdbpreds.loc[lambda x: (x["pred"] == 1) & (x["label"] == 0)] )
            fn = len( pdbpreds.loc[lambda x: (x["pred"] == 0) & (x["label"] == 1)] )
            if tp + fn == 0:
                fn = 1 # There's at least 1 allo. pocket per PDB
        else:
            tp, fp = 0, 0
            fn = 1 # There's at least 1 allo. pocket per PDB

        if total == 0 or not modeld["all_pockets_in_output"]:
            preds[pdb] = {
                "tp": tp,
                "fn": fn,
                "fp": fp
            }
        else:
            preds[pdb] = {
                "total": total,
                "tp": tp,
                "fn": fn,
                "fp": fp
            }

    models_preds[model] = preds

models_preds

    prob
0      0
1      0
2      0
3      0
4      0
5      1
6      0
7      0
8      0
9      0
10     0
11     0
12     0
13     0
14     0
0     0
1     0
2     0
3     0
4     0
5     1
6     0
7     0
8     0
9     0
10    0
11    0
12    0
13    0
14    0
Name: pred, dtype: int64
    prob
15     0
16     0
17     0
18     0
19     0
..   ...
76     0
77     0
78     1
79     0
80     0

[66 rows x 1 columns]
15    0
16    0
17    0
18    0
19    0
     ..
76    0
77    0
78    1
79    0
80    0
Name: pred, Length: 66, dtype: int64
    prob
81     0
82     1
83     0
84     0
85     0
86     0
81    0
82    1
83    0
84    0
85    0
86    0
Name: pred, dtype: int64
    prob
87     0
88     1
89     0
90     0
91     0
92     0
93     0
94     0
95     0
96     0
87    0
88    1
89    0
90    0
91    0
92    0
93    0
94    0
95    0
96    0
Name: pred, dtype: int64
     prob
97      0
98      0
99      0
100     0
101     0
102     0
103     0
104     0
105     0
106     0
107  

{'model5': {'7gqu': {'total': 15, 'tp': 1, 'fn': 0, 'fp': 0},
  '7yg5': {'total': 66, 'tp': 0, 'fn': 1, 'fp': 1},
  '8aq6': {'total': 6, 'tp': 1, 'fn': 0, 'fp': 0},
  '8f4s': {'total': 10, 'tp': 1, 'fn': 0, 'fp': 0},
  '8jp0': {'total': 34, 'tp': 1, 'fn': 0, 'fp': 0},
  '8qni': {'total': 17, 'tp': 1, 'fn': 0, 'fp': 0},
  '8uk6': {'total': 30, 'tp': 1, 'fn': 0, 'fp': 0},
  '8v81': {'total': 45, 'tp': 1, 'fn': 0, 'fp': 0},
  '9dnm': {'total': 22, 'tp': 0, 'fn': 1, 'fp': 1}},
 'allositepro': {'7gqu': {'tp': 1, 'fn': 0, 'fp': 0},
  '7yg5': {'tp': 0, 'fn': 1, 'fp': 1},
  '8aq6': {'tp': 0, 'fn': 1, 'fp': 1},
  '8f4s': {'tp': 1, 'fn': 0, 'fp': 0},
  '8jp0': {'tp': 1, 'fn': 0, 'fp': 0},
  '8qni': {'tp': 1, 'fn': 0, 'fp': 0},
  '8uk6': {'tp': 1, 'fn': 0, 'fp': 0},
  '8v81': {'tp': 1, 'fn': 0, 'fp': 0},
  '9dnm': {'tp': 0, 'fn': 1, 'fp': 0}},
 'stingallo': {'7gqu': {'tp': 0, 'fn': 1, 'fp': 1},
  '7yg5': {'tp': 0, 'fn': 1, 'fp': 0},
  '8aq6': {'tp': 0, 'fn': 1, 'fp': 0},
  '8f4s': {'tp': 0, 'fn':

In [66]:
from sklearn.metrics import matthews_corrcoef, f1_score, confusion_matrix

In [67]:
models_metrics = {}

for model, preds in models_preds.items():
    df = pd.DataFrame(preds).T
    
    if models[model]["all_pockets_in_output"]:
        y_true = [1] * df["tp"].sum() + [1] * df["fn"].sum() + [0] * df["fp"].sum() + [0] * (df["total"].sum() - df[["tp", "fn", "fp"]].sum().sum())
        y_pred = [1] * df["tp"].sum() + [0] * df["fn"].sum() + [1] * df["fp"].sum() + [0] * (df["total"].sum() - df[["tp", "fn", "fp"]].sum().sum())

        models_metrics[model] = {
            "model": model,
            "tp": df["tp"].sum(),
            "fn": df["fn"].sum(),
            "fp": df["fp"].sum(),
            "mcc": matthews_corrcoef(y_true, y_pred),
            "macro-f1": f1_score(y_true, y_pred, average="macro"),
            "confmat": pd.DataFrame(confusion_matrix(y_true, y_pred))
        }
        
    else:
        models_metrics[model] = {
            "model": model,
            "tp": df["tp"].sum(),
            "fn": df["fn"].sum(),
            "fp": df["fp"].sum(),
        }

models_metrics = pd.DataFrame(models_metrics).T.sort_values(["tp", "mcc"], ascending=False)
models_metrics

model tp fn fp       mcc  macro-f1  \
model5                    model5  7  2  2  0.769303  0.884652   
allositepro          allositepro  6  3  2       NaN       NaN   
passer_ensemble  passer_ensemble  5  4  4  0.545377  0.772689   
allo                        allo  5  4  4  0.533578  0.766789   
passer_automl      passer_automl  4  5  5  0.431722  0.715861   
alloses                  alloses  3  6  6  0.318027  0.659014   
deepallo                deepallo  2  7  7  0.204456  0.602228   
mefallosite          mefallosite  2  7  7   0.20075  0.600375   
passer_rank          passer_rank  1  8  8  0.090755  0.545377   
stingallo              stingallo  1  8  1       NaN       NaN   

                                       confmat  
model5                0  1
0  234  2
1    2  7  
allositepro                                NaN  
passer_ensemble       0  1
0  389  4
1    4  5  
allo                  0  1
0  178  4
1    4  5  
passer_automl         0  1
0  388  5
1    5  4  
alloses               0  1
0  386  6
1    6  3  
deepallo              0  1
0  387  7
1    7  2  
mefallosite           0  1
0  319  7
1    7  2  
passer_rank           0  1
0  385  8
1    8  1  
stingallo                                  NaN

In [78]:
models_metrics.infer_objects().to_csv("models_metrics_top1.csv", index=False, sep="\t", decimal=",")